In [47]:
import numpy as np 
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
import os

import regex
from wordcloud import WordCloud
from nltk.corpus import stopwords 
from nltk.tokenize import WordPunctTokenizer
from string import punctuation
from nltk.stem import WordNetLemmatizer

In [2]:
data = pd.read_csv('C:\\Users\\Utkarsh\\Desktop\\Classification of Cyber Bulling using NLP\\Dataset\\data.csv')

In [3]:
data.head()

content  annotation/label/0
0                             Get fucking real dude.                   1
1   She is as dirty as they come  and that crook ...                   1
2   why did you fuck it up. I could do it all day...                   1
3   Dude they dont finish enclosing the fucking s...                   1
4   WTF are you talking about Men? No men thats n...                   1

In [4]:
data.info()


<class 'pandas.core.frame.DataFrame'>
RangeIndex: 20001 entries, 0 to 20000
Data columns (total 2 columns):
 #   Column              Non-Null Count  Dtype 
---  ------              --------------  ----- 
 0   content             20001 non-null  object
 1   annotation/label/0  20001 non-null  int64 
dtypes: int64(1), object(1)
memory usage: 312.6+ KB


In [5]:
data.isna().sum()


content               0
annotation/label/0    0
dtype: int64

In [6]:
import numpy as np
import pandas as pd
import tensorflow as tf
import seaborn as sns
import transformers

import nltk
import re


from matplotlib import pyplot as plt
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score, roc_auc_score, roc_curve

plt.style.use('seaborn')

C:\Users\Utkarsh\AppData\Local\Temp\ipykernel_18688\1554521867.py:15: MatplotlibDeprecationWarning: The seaborn styles shipped by Matplotlib are deprecated since 3.6, as they no longer correspond to the styles shipped by seaborn. However, they will remain available as 'seaborn-v0_8-<style>'. Alternatively, directly use the seaborn API instead.
  plt.style.use('seaborn')


In [7]:
print(tf.__version__)
print(tf.config.list_physical_devices('GPU'))

2.14.0
[]


In [8]:
from transformers import TFXLNetModel, XLNetTokenizer


In [9]:
xlnet_model = 'xlnet-large-cased'
xlnet_tokenizer = XLNetTokenizer.from_pretrained(xlnet_model)

In [10]:
number_of_classes = 1 #len(names)
number_of_classes

1

In [12]:
data.rename(columns = {'annotation/label/0':'Class'}, inplace = True)


In [ ]:
 
# count plot on single categorical variable
sns.barplot(x = 'Class', y = 'content', data = data) 
# Show the plot
plt.show()

In [11]:
def create_xlnet(mname):
    """ Creates the model. It is composed of the XLNet main block and then
    a classification head its added
    """
    # Define token ids as inputs
    word_inputs = tf.keras.Input(shape=(120,), name='word_inputs', dtype='int32')

    # Call XLNet model
    xlnet = TFXLNetModel.from_pretrained(mname)
    xlnet_encodings = xlnet(word_inputs)[0]

    # CLASSIFICATION HEAD 
    # Collect last step from last hidden state (CLS)
    doc_encoding = tf.squeeze(xlnet_encodings[:, -1:, :], axis=1)
    # Apply dropout for regularization
    doc_encoding = tf.keras.layers.Dropout(.1)(doc_encoding)
    # Final output 
    outputs = tf.keras.layers.Dense(number_of_classes, activation='sigmoid', name='outputs')(doc_encoding)

    # Compile model
    model = tf.keras.Model(inputs=[word_inputs], outputs=[outputs])
    model.compile(optimizer=tf.keras.optimizers.Adam(lr=2e-5), loss='binary_crossentropy', metrics=['accuracy', tf.keras.metrics.Precision(), tf.keras.metrics.Recall()])

    return model

In [12]:
xlnet = create_xlnet(xlnet_model)

C:\Users\Utkarsh\AppData\Roaming\Python\Python311\site-packages\keras\src\initializers\initializers.py:120: UserWarning: The initializer TruncatedNormal is unseeded and being called multiple times, which will return identical values each time (even if the initializer is unseeded). Please update your code to provide a seed to the initializer, or avoid using the same initializer instance more than once.
  warnings.warn(
Some layers from the model checkpoint at xlnet-large-cased were not used when initializing TFXLNetModel: ['lm_loss']
- This IS expected if you are initializing TFXLNetModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing TFXLNetModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Al

In [13]:
xlnet.summary()

Model: "model"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 word_inputs (InputLayer)    [(None, 120)]             0         
                                                                 
 tfxl_net_model (TFXLNetMod  TFXLNetModelOutput(last   360268800 
 el)                         _hidden_state=(None, 12             
                             0, 1024),                           
                              mems=((120, None, 1024             
                             ),                                  
                              (120, None, 1024),                 
                              (120, None, 1024),                 
                              (120, None, 1024),                 
                              (120, None, 1024),                 
                              (120, None, 1024),                 
                              (120, None, 1024),             

In [23]:
# data['Class']
data

content  Class
0                                 Get fucking real dude.      1
1       She is as dirty as they come  and that crook ...      1
2       why did you fuck it up. I could do it all day...      1
3       Dude they dont finish enclosing the fucking s...      1
4       WTF are you talking about Men? No men thats n...      1
...                                                  ...    ...
19996    I dont. But what is complaining about it goi...      0
19997   Bahah  yeah i&;m totally just gonna&; get pis...      0
19998       hahahahaha >:) im evil mwahahahahahahahahaha      0
19999            What&;s something unique about Ohio? :)      0
20000              Who is the biggest gossiper you know?      0

[20001 rows x 2 columns]

In [59]:
from sklearn import preprocessing

le = preprocessing.LabelEncoder()
y = le.fit_transform(data['Class'])

In [60]:
from sklearn.model_selection import train_test_split
x_train, x_test, y_train, y_test = train_test_split(x_train, y_train, test_size=0.33, random_state=1)

In [61]:
x_train = data.content
y_train = data.Class

In [62]:
x_train = np.array(x_train)
y_train = np.array(y_train)

In [63]:
from nltk.stem import WordNetLemmatizer
from nltk import pos_tag
lemmatizer = WordNetLemmatizer()

In [64]:
from nltk.corpus import wordnet
def get_simple_pos(tag):
    
    if tag.startswith('J'):
        return wordnet.ADJ
    elif tag.startswith('V'):
        return wordnet.VERB
    elif tag.startswith('N'):
        return wordnet.NOUN
    elif tag.startswith('R'):
        return wordnet.ADV
    else:
        return wordnet.NOUN

In [65]:
from nltk.corpus import stopwords
import string
stops = set(stopwords.words('english'))
punctuations = list(string.punctuation)
stops.update(punctuations)
# stops, string.punctuation

In [66]:
def clean_review(words):
    output_words = []
    for w in words:
        if w.lower() not in stops:
            pos = pos_tag([w])
            clean_word = lemmatizer.lemmatize(w, pos = get_simple_pos(pos[0][1]))
            output_words.append(clean_word.lower())
    return " ".join(output_words)

In [67]:
from nltk.tokenize import word_tokenize 
x_train = [clean_review(word_tokenize(i)) for i in x_train]

In [68]:
x_test = [clean_review(word_tokenize(i)) for i in x_test]

In [54]:
def make_wordcloud(words,title):
    cloud = WordCloud(width=1920, height=1080,max_font_size=200, max_words=300, background_color="white").generate(words)
    plt.figure(figsize=(20,20))
    plt.imshow(cloud, interpolation="gaussian")
    plt.axis("off") 
    plt.title(title, fontsize=60)
    plt.show()

In [ ]:
all_text = " ".join(data[data.Class == "Class"].filtered_text) 
make_wordcloud(all_text, "Class")

In [74]:
def get_inputs(text, tokenizer, max_len=120):
    """ Gets tensors from text using the tokenizer provided"""
    inps = [tokenizer.encode_plus(t, max_length=max_len, pad_to_max_length=True, add_special_tokens=True) for t in text]
    inp_tok = np.array([a['input_ids'] for a in inps])
    ids = np.array([a['attention_mask'] for a in inps])
    segments = np.array([a['token_type_ids'] for a in inps])
    return inp_tok, ids, segments

In [75]:
def warmup(epoch, lr):

    return max(lr +1e-6, 2e-5)

def plot_metrics(pred, true_labels):
    acc = accuracy_score(true_labels, np.array(pred.flatten() >= .5, dtype='int'))
    fpr, tpr, thresholds = roc_curve(true_labels, pred)
    auc = roc_auc_score(true_labels, pred)

    fig, ax = plt.subplots(1, figsize=(8,8))
    ax.plot(fpr, tpr, color='red')
    ax.plot([0,1], [0,1], color='black', linestyle='--')
    ax.set_title(f"AUC: {auc}\nACC: {acc}");
    return fig

In [76]:
inp_tok, ids, segments = get_inputs(x_train, xlnet_tokenizer)

In [77]:
callbacks = [
    tf.keras.callbacks.EarlyStopping(monitor='val_accuracy', patience=4, min_delta=0.02, restore_best_weights=True),
    tf.keras.callbacks.LearningRateScheduler(warmup, verbose=0),
    tf.keras.callbacks.ReduceLROnPlateau(monitor='val_accuracy', factor=1e-6, patience=2, verbose=0, mode='auto', min_delta=0.001, cooldown=0, min_lr=1e-6)
]

In [79]:
tf.config.run_functions_eagerly(True)


In [80]:
hist = xlnet.fit(x=inp_tok, y=y_train, epochs=4, batch_size=2, validation_split=.15, callbacks=callbacks)

C:\Users\Utkarsh\AppData\Roaming\Python\Python311\site-packages\tensorflow\python\data\ops\structured_function.py:258: UserWarning: Even though the `tf.config.experimental_run_functions_eagerly` option is set, this option does not apply to tf.data functions. To force eager execution of tf.data functions, please use `tf.data.experimental.enable_debug_mode()`.
  warnings.warn(


Epoch 1/4


   1/8500 [..............................] - ETA: 48:17:38 - loss: 19.8070 - accuracy: 0.0000e+00 - precision: 0.0000e+00 - recall: 0.0000e+00WARNING:tensorflow:Gradients do not exist for variables ['tfxl_net_model/transformer/mask_emb:0', 'tfxl_net_model/transformer/layer_._0/rel_attn/r_s_bias:0', 'tfxl_net_model/transformer/layer_._0/rel_attn/seg_embed:0', 'tfxl_net_model/transformer/layer_._1/rel_attn/r_s_bias:0', 'tfxl_net_model/transformer/layer_._1/rel_attn/seg_embed:0', 'tfxl_net_model/transformer/layer_._2/rel_attn/r_s_bias:0', 'tfxl_net_model/transformer/layer_._2/rel_attn/seg_embed:0', 'tfxl_net_model/transformer/layer_._3/rel_attn/r_s_bias:0', 'tfxl_net_model/transformer/layer_._3/rel_attn/seg_embed:0', 'tfxl_net_model/transformer/layer_._4/rel_attn/r_s_bias:0', 'tfxl_net_model/transformer/layer_._4/rel_attn/seg_embed:0', 'tfxl_net_model/transformer/layer_._5/rel_attn/r_s_bias:0', 'tfxl_net_model/transformer/layer_._5/rel_attn/seg_embed:0', 'tfxl_net_model/transformer/layer_

   2/8500 [..............................] - ETA: 47:12:04 - loss: 18.2152 - accuracy: 0.2500 - precision: 0.0000e+00 - recall: 0.0000e+00    WARNING:tensorflow:Gradients do not exist for variables ['tfxl_net_model/transformer/mask_emb:0', 'tfxl_net_model/transformer/layer_._0/rel_attn/r_s_bias:0', 'tfxl_net_model/transformer/layer_._0/rel_attn/seg_embed:0', 'tfxl_net_model/transformer/layer_._1/rel_attn/r_s_bias:0', 'tfxl_net_model/transformer/layer_._1/rel_attn/seg_embed:0', 'tfxl_net_model/transformer/layer_._2/rel_attn/r_s_bias:0', 'tfxl_net_model/transformer/layer_._2/rel_attn/seg_embed:0', 'tfxl_net_model/transformer/layer_._3/rel_attn/r_s_bias:0', 'tfxl_net_model/transformer/layer_._3/rel_attn/seg_embed:0', 'tfxl_net_model/transformer/layer_._4/rel_attn/r_s_bias:0', 'tfxl_net_model/transformer/layer_._4/rel_attn/seg_embed:0', 'tfxl_net_model/transformer/layer_._5/rel_attn/r_s_bias:0', 'tfxl_net_model/transformer/layer_._5/rel_attn/seg_embed:0', 'tfxl_net_model/transformer/layer_

   3/8500 [..............................] - ETA: 47:27:04 - loss: 12.1530 - accuracy: 0.5000 - precision: 0.0000e+00 - recall: 0.0000e+00WARNING:tensorflow:Gradients do not exist for variables ['tfxl_net_model/transformer/mask_emb:0', 'tfxl_net_model/transformer/layer_._0/rel_attn/r_s_bias:0', 'tfxl_net_model/transformer/layer_._0/rel_attn/seg_embed:0', 'tfxl_net_model/transformer/layer_._1/rel_attn/r_s_bias:0', 'tfxl_net_model/transformer/layer_._1/rel_attn/seg_embed:0', 'tfxl_net_model/transformer/layer_._2/rel_attn/r_s_bias:0', 'tfxl_net_model/transformer/layer_._2/rel_attn/seg_embed:0', 'tfxl_net_model/transformer/layer_._3/rel_attn/r_s_bias:0', 'tfxl_net_model/transformer/layer_._3/rel_attn/seg_embed:0', 'tfxl_net_model/transformer/layer_._4/rel_attn/r_s_bias:0', 'tfxl_net_model/transformer/layer_._4/rel_attn/seg_embed:0', 'tfxl_net_model/transformer/layer_._5/rel_attn/r_s_bias:0', 'tfxl_net_model/transformer/layer_._5/rel_attn/seg_embed:0', 'tfxl_net_model/transformer/layer_._6/

...

 355/8500 [>.............................] - ETA: 59:57:12 - loss: 1.8827 - accuracy: 0.5211 - precision: 0.4756 - recall: 0.4492WARNING:tensorflow:Gradients do not exist for variables ['tfxl_net_model/transformer/mask_emb:0', 'tfxl_net_model/transformer/layer_._0/rel_attn/r_s_bias:0', 'tfxl_net_model/transformer/layer_._0/rel_attn/seg_embed:0', 'tfxl_net_model/transformer/layer_._1/rel_attn/r_s_bias:0', 'tfxl_net_model/transformer/layer_._1/rel_attn/seg_embed:0', 'tfxl_net_model/transformer/layer_._2/rel_attn/r_s_bias:0', 'tfxl_net_model/transformer/layer_._2/rel_attn/seg_embed:0', 'tfxl_net_model/transformer/layer_._3/rel_attn/r_s_bias:0', 'tfxl_net_model/transformer/layer_._3/rel_attn/seg_embed:0', 'tfxl_net_model/transformer/layer_._4/rel_attn/r_s_bias:0', 'tfxl_net_model/transformer/layer_._4/rel_attn/seg_embed:0', 'tfxl_net_model/transformer/layer_._5/rel_attn/r_s_bias:0', 'tfxl_net_model/transformer/layer_._5/rel_attn/seg_embed:0', 'tfxl_net_model/transformer/layer_._6/rel_attn/

 356/8500 [>.............................] - ETA: 59:56:44 - loss: 1.8804 - accuracy: 0.5197 - precision: 0.4740 - recall: 0.4479WARNING:tensorflow:Gradients do not exist for variables ['tfxl_net_model/transformer/mask_emb:0', 'tfxl_net_model/transformer/layer_._0/rel_attn/r_s_bias:0', 'tfxl_net_model/transformer/layer_._0/rel_attn/seg_embed:0', 'tfxl_net_model/transformer/layer_._1/rel_attn/r_s_bias:0', 'tfxl_net_model/transformer/layer_._1/rel_attn/seg_embed:0', 'tfxl_net_model/transformer/layer_._2/rel_attn/r_s_bias:0', 'tfxl_net_model/transformer/layer_._2/rel_attn/seg_embed:0', 'tfxl_net_model/transformer/layer_._3/rel_attn/r_s_bias:0', 'tfxl_net_model/transformer/layer_._3/rel_attn/seg_embed:0', 'tfxl_net_model/transformer/layer_._4/rel_attn/r_s_bias:0', 'tfxl_net_model/transformer/layer_._4/rel_attn/seg_embed:0', 'tfxl_net_model/transformer/layer_._5/rel_attn/r_s_bias:0', 'tfxl_net_model/transformer/layer_._5/rel_attn/seg_embed:0', 'tfxl_net_model/transformer/layer_._6/rel_attn/

 357/8500 [>.............................] - ETA: 59:56:16 - loss: 1.8796 - accuracy: 0.5196 - precision: 0.4740 - recall: 0.4465WARNING:tensorflow:Gradients do not exist for variables ['tfxl_net_model/transformer/mask_emb:0', 'tfxl_net_model/transformer/layer_._0/rel_attn/r_s_bias:0', 'tfxl_net_model/transformer/layer_._0/rel_attn/seg_embed:0', 'tfxl_net_model/transformer/layer_._1/rel_attn/r_s_bias:0', 'tfxl_net_model/transformer/layer_._1/rel_attn/seg_embed:0', 'tfxl_net_model/transformer/layer_._2/rel_attn/r_s_bias:0', 'tfxl_net_model/transformer/layer_._2/rel_attn/seg_embed:0', 'tfxl_net_model/transformer/layer_._3/rel_attn/r_s_bias:0', 'tfxl_net_model/transformer/layer_._3/rel_attn/seg_embed:0', 'tfxl_net_model/transformer/layer_._4/rel_attn/r_s_bias:0', 'tfxl_net_model/transformer/layer_._4/rel_attn/seg_embed:0', 'tfxl_net_model/transformer/layer_._5/rel_attn/r_s_bias:0', 'tfxl_net_model/transformer/layer_._5/rel_attn/seg_embed:0', 'tfxl_net_model/transformer/layer_._6/rel_attn/

 358/8500 [>.............................] - ETA: 59:55:22 - loss: 1.8761 - accuracy: 0.5196 - precision: 0.4740 - recall: 0.4451

KeyboardInterrupt: 

In [ ]:
inp_tok, ids, segments = get_inputs(x_test, xlnet_tokenizer)

In [82]:
preds = xlnet.predict(inp_tok, verbose=True)

  2/626 [..............................] - ETA: 4:59:03

KeyboardInterrupt: 

In [ ]:
pred_analysis_df = pd.DataFrame({'tweet':X_test.values, 'pred':preds.flatten(), 'real':y_test})
pred_analysis_df['rounded'] = np.array(pred_analysis_df['pred'] > 0.5, dtype='int')
diff = pred_analysis_df[pred_analysis_df['real'] != pred_analysis_df['rounded']]

In [ ]:
idx = 44

tweet, real, pred = diff.iloc[idx, [0,2,3]]
print(tweet)
print("PRED: " + str(pred))
print("REAL: " + str(real))

In [ ]:
from sklearn import metrics
confusion_matrix = metrics.confusion_matrix(y_test, y_pred)
print(confusion_matrix)

In [ ]:
from sklearn.metrics import classification_report
print(classification_report(y_test, y_pred))

In [ ]:
import matplotlib.pyplot as plt
from sklearn.metrics import roc_curve

fpr, tpr, thresholds = roc_curve(y_true=y_test, y_score=y_pred)
plt.xlabel("False postive")
plt.ylabel("True postive")
plt.plot(fpr, tpr)
plt.show()